In [1]:
#| default_exp reading
%load_ext autoreload
%autoreload 2

import sys
from fastcore.xtras import Path
# Insert in Path Project Directory
sys.path.insert(0, str(Path().cwd().parent))

# Leitura
> Este módulo concentra funções para a leitura dos diversos arquivos que compõe a base de dados

* `STEL` - Serviços Privados de Telecomunicações
* `RADCOM` - Serviço de Radiodifusão Comunitária
* `MOSAICO` - Demais serviços de Radiodifusão, e.g. TV, RTV, FM, AM, etc.
* `AERONAUTICA` - Consolidação de diversas bases de dados públicas da aeronáutica 

In [2]:
#| export
from typing import Union
from pathlib import Path

import pandas as pd
from pyarrow import ArrowInvalid
import pyodbc
from pymongo import MongoClient

from extracao.updates import (
update_mosaico, update_stel, update_radcom, update_base, update_telecom
)

In [3]:
#| export
def _read_df(folder: Union[str, Path], stem: str) -> pd.DataFrame:
    """Lê o dataframe formado por folder / stem.[parquet.gzip | fth | xslx]"""
    file = Path(f"{folder}/{stem}.parquet.gzip")
    try:
        df = pd.read_parquet(file)
    except (ArrowInvalid, FileNotFoundError):
        file = Path(f"{folder}/{stem}.fth")
        try:
            df = pd.read_feather(file)
        except (ArrowInvalid, FileNotFoundError):
            file = Path(f"{folder}/{stem}.xlsx")
            try:
                df = pd.read_excel(file, engine="openpyxl", sheet_name="DataBase")
            except Exception as e:
                raise ValueError(f"Error when reading {file}") from e
    return df

## MOSAICO
> O mosaico atualmente é composto por 2 bases complementares originárias de um banco `MongoDB`: 

-  `Estações`
- `Plano Básico`

In [4]:
#| export
def read_mosaico(folder: Union[str, Path], # Pasta onde ler/salvar os dados
                 conn: MongoClient = None, # Objeto de Conexão com o banco MongoDB, atualiza os dados caso válido
) -> pd.DataFrame: # Dataframe com os dados do mosaico
    """Lê o banco de dados salvo localmente do MOSAICO e opcionalmente o atualiza."""
    return update_mosaico(conn, folder) if conn else _read_df(folder, "mosaico")

In [5]:
#| hide
folder = Path.cwd().parent / 'dados'

In [6]:
#|eval: false
from pandas_profiling import ProfileReport

In [7]:
#|eval: false
#|code_fold: true
mosaico = read_mosaico(folder)
mosaico['Frequência'] = mosaico['Frequência'].astype('category')
mosaico_profile = ProfileReport(mosaico, config_file='report_config.yaml', title='MOSAICO')
mosaico_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## LICENCIAMENTO
> A Base licenciamento é composta de serviços privados de telecomunicações, tanto antigos migrados do STEL como novos para um novo banco de dados `MongoDB`

In [8]:
#| export
def read_telecom(folder: Union[str, Path], # Pasta onde ler/salvar os dados
                conn: MongoClient = None, # Objeto de Conexão com o banco MongoDB, atualiza os dados caso válido
) -> pd.DataFrame: # Dataframe com os dados do mosaico
    """Lê o banco de dados salvo localmente do LICENCIAMENTO e opcionalmente o atualiza."""
    return update_telecom(conn, folder) if conn else _read_df(folder, "telecom")

In [9]:
#|eval: false
#|code_fold: true
telecom = read_telecom(folder)
telecom['Frequência'] = telecom['Frequência'].astype('category')
telecom_profile = ProfileReport(telecom, config_file='report_config.yaml', title='Telecomunicações')
telecom_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

##  RADCOM

In [10]:
#| export
def read_radcom(
    folder: Union[str, Path], # Pasta onde ler/salvar os dados
    conn: pyodbc.Connection = None, # Objeto de conexão de banco, atualiza os dados caso válido
) -> pd.DataFrame: # Dataframe com os dados de RADCOM
    """Lê o banco de dados salvo localmente de RADCOM. Opcionalmente o atualiza pelo Banco de Dados ANATELBDRO05 caso `update = True` ou não exista o arquivo local"""
    return update_radcom(conn, folder) if conn else _read_df(folder, "radcom")

In [11]:
#|eval: false
#|code_fold: true
radcom = read_radcom(folder)
radcom['Frequência'] = radcom['Frequência'].astype('category')
radcom_profile = ProfileReport(radcom, config_file='report_config.yaml', title='RADCOM')
radcom_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## STEL

In [12]:
#| export
def read_stel(folder: Union[str, Path], # Pasta onde ler/salvar os dados
              conn: pyodbc.Connection = None, # Objeto de conexão de banco. Atualiza os dados caso válido
) -> pd.DataFrame: # Dataframe com os dados do STEL
    """Lê o banco de dados salvo localmente do STEL. 
       Opcionalmente o atualiza pelo Banco de Dados ANATELBDRO05
      caso `update = True` ou não exista o arquivo local"""
    return update_stel(conn, folder) if conn else _read_df(folder, "stel")

In [13]:
#|eval: false
#|code_fold: true
stel = read_stel(folder)
stel['Frequência'] = stel['Frequência'].astype('category')
stel_profile = ProfileReport(stel, config_file='report_config.yaml', title='STEL')
stel_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Bases Externas da Aeronáutica

In [14]:
#| export
def read_icao(folder: Union[str, Path], # Pasta onde ler/salvar os dados
              update: bool = False, # Atualiza os dados caso `True`
) -> pd.DataFrame: # Dataframe com os dados do ICAO
    """Lê a base de dados do Frequency Finder e Canalização VOR/ILS/DME"""
    if update:
        # TODO: atualizar a base de dados do Frequency Finder e Canalização VOR/ILS/DME
        # update_icao(folder)
        raise NotImplementedError(
            "Atualizar da base de dados do Frequency Finder e Canalização VOR/ILS/DME não implementado"
        )
    return _read_df(folder, "icao")


In [15]:
#|eval: false
#|code_fold: true
icao = read_icao(folder)
icao['Frequency'] = icao['Frequency'].astype('category')
icao_profile = ProfileReport(icao, config_file='report_config.yaml', title='ICAO')
icao_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [16]:
#| export
def read_aisw(folder: Union[str, Path], # Pasta onde ler/salvar os dados
              update: bool = False, # Atualiza os dados caso `True`
) -> pd.DataFrame: # Dataframe com os dados do AISWEB
    """Fontes da informação: AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    if update:
        # TODO: Atualizar a base de dados do AISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME
        # update_pmec(folder)
        raise NotImplementedError(
            "Atualizar da base de dados do Frequency Finder e Canalização VOR/ILS/DME não implementado"
        )
    return _read_df(folder, "aisw")



In [17]:
#|eval: false
#|code_fold: true
aisw = read_aisw(folder)
aisw['Frequency'] = aisw['Frequency'].astype('category')
aisw_profile = ProfileReport(aisw, config_file='report_config.yaml', title='AISWEB')
aisw_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [18]:
#| export
def read_aisg(folder: Union[str, Path], # Pasta onde ler/salvar os dados
update: bool = False, # Atualiza os dados caso `True`
) -> pd.DataFrame: # Dataframe com os dados do GEOAISWEB
    """Fontes da informação: GEOAISWEB, REDEMET, Ofício nº 2/SSARP/14410 e Canalização VOR/ILS/DME."""
    if update:
        # TODO: Atualizar a base de dados do GEOAISWEB
        # update_geo(folder)
        raise NotImplementedError(
            "Atualizar da base de dados do Frequency Finder e Canalização VOR/ILS/DME não implementado"
        )
    return _read_df(folder, "aisg")

In [19]:
#|eval: false
#|code_fold: true
aisg = read_aisg(folder)
aisg['Frequency'] = aisg['Frequency'].astype('category')
aisg_profile = ProfileReport(aisg, config_file='report_config.yaml', title='GEOAISWEB')
aisg_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [20]:
#| export
def read_aero(
    folder: Union[str, Path], # Pasta onde ler/salvar os dados
update: bool = False, # Atualiza os dados caso `True`
) -> pd.DataFrame: # Dataframe com os dados mesclados das 3 bases da Aeronáutica anteriores
    """Lê os arquivos de dados da aeronáutica e retorna os registros comuns e únicos"""
    if update:
        # TODO: Atualizar a base de dados do GEOAISWEB
        # update_geo(folder)
        raise NotImplementedError(
            "Atualização programática das bases de Dados da Aeronáutica não implementada"
        )
    
    return _read_df(folder, "aero")

In [21]:
#|eval: false
#|code_fold: true
aero= read_aero(folder)
aero['Frequency'] = aero['Frequency'].astype('category')
aero_profile = ProfileReport(aero, config_file='report_config.yaml', title='AERONAUTICA')
aero_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Base Consolidada

In [22]:
#| export
def read_base(
    folder: Union[str, Path], 
    conn: pyodbc.Connection = None, # Objeto de conexão do banco SQL Server
    clientMongoDB: MongoClient = None, # Objeto de conexão do banco MongoDB
) -> pd.DataFrame:
    """Lê a base de dados e opcionalmente a atualiza antes da leitura casos as conexões de banco sejam válidas"""
    return update_base(conn, clientMongoDB, folder) if all([conn, clientMongoDB]) else _read_df(folder, "base")

In [23]:
#|eval: false
#|code_fold: true
base = read_base(folder)
base['Frequência'] = base['Frequência'].astype('category')
base_profile = ProfileReport(base, config_file='report_config.yaml', title='Base Consolidada')
base_profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]